# **Imports**

In [4]:
import os
import shutil
import os
import xml.etree.ElementTree as ET
from random import shuffle
from tqdm import tqdm
path = os.getcwd()

In [5]:
path

'/home/jovyan/Carlos_Gonzalez/YOLO'

# **YOLO format**

Como vamos a trabajar con modelos tipo YOLO, tenemos que adaptar los dataset al formato YOLO tanto la estructuración de las carpetas y el tipo de anotaciones. Hay que saber que las anotaciones de estos tipos de dataset para modelos de detección contienen información de las cajas o Boundary Boxes de donde se encuentra cada uno de los objetos y de la clase a la que pertenece.

El formato YOLO ([paper](https://arxiv.org/pdf/1506.02640)) esta compuesto por una serie de carpetas y subcarpetas:
* name_dataset
   * images
      * train
      * valid
      * test
   * labels
      * train
      * valid
      * test
Las imagenes en los casos que abordaremos están en formato .jpg, mientras que los labels tienen que pasar a tener extensión .txt. Para cada imagen en cada una de las subcarpetas tiene un fichero .txt en la subcarpeta correspondiente dentro de label (con el mismo nombre pero con la extensión .txt).

El formato YOLO es:

"class x_center y_center width height"

Donde class es un numero (int) que se corresponde con una clase en concreto, por otro lado x_center, y_center, width y height tienen que estar normalizados con respecto a la imagen, en el que se impone la condición de que tienen que estar entre (0,1] los valores de x_center e y_center

# **Download PASCAL Dataset**

### Download Dataset

Desacaramos el dataset de **PASCAL** del siguiente enlace, en forma de fichero .tar http://host.robots.ox.ac.uk/pascal/VOC/voc2012/VOCtrainval_11-May-2012.tar

In [12]:
!wget http://host.robots.ox.ac.uk/pascal/VOC/voc2012/VOCtrainval_11-May-2012.tar

--2024-05-06 14:51:08--  http://host.robots.ox.ac.uk/pascal/VOC/voc2012/VOCtrainval_11-May-2012.tar
Resolving host.robots.ox.ac.uk (host.robots.ox.ac.uk)... 129.67.94.152
Connecting to host.robots.ox.ac.uk (host.robots.ox.ac.uk)|129.67.94.152|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1999639040 (1.9G) [application/x-tar]
Saving to: ‘VOCtrainval_11-May-2012.tar’

VOCtrainval_11-May- 100%[===================>]   1.86G  11.7MB/s    in 3m 14s  

2024-05-06 14:54:35 (9.81 MB/s) - ‘VOCtrainval_11-May-2012.tar’ saved [1999639040/1999639040]



Descomprimimos el archivo .tar

In [ ]:
!tar -xvf VOCtrainval_11-May-2012.tar

VOCdevkit/
VOCdevkit/VOC2012/
VOCdevkit/VOC2012/Annotations/
VOCdevkit/VOC2012/Annotations/2007_000027.xml
tar: VOCdevkit/VOC2012/Annotations/2007_000027.xml: Cannot change ownership to uid 0, gid 0: Operation not permitted
VOCdevkit/VOC2012/Annotations/2007_000032.xml
tar: VOCdevkit/VOC2012/Annotations/2007_000032.xml: Cannot change ownership to uid 0, gid 0: Operation not permitted
VOCdevkit/VOC2012/Annotations/2007_000033.xml
tar: VOCdevkit/VOC2012/Annotations/2007_000033.xml: Cannot change ownership to uid 0, gid 0: Operation not permitted
VOCdevkit/VOC2012/Annotations/2007_000039.xml
tar: VOCdevkit/VOC2012/Annotations/2007_000039.xml: Cannot change ownership to uid 0, gid 0: Operation not permitted
VOCdevkit/VOC2012/Annotations/2007_000042.xml
tar: VOCdevkit/VOC2012/Annotations/2007_000042.xml: Cannot change ownership to uid 0, gid 0: Operation not permitted
VOCdevkit/VOC2012/Annotations/2007_000061.xml
tar: VOCdevkit/VOC2012/Annotations/2007_000061.xml: Cannot change ownership to

Eliminamos el fichero .tar por dejar la carpeta más limpia

In [ ]:
os.remove('VOCtrainval_11-May-2012.tar')

### Convert annotations to YOLO format

En el siguiente trozo de código nos centramos en leer la carpeta de Annotations de VOCdeckit, donde los ficheros están en formato .xml, del cual hay que extraer la información relevante para poder convertirlo a formato YOLO.

En estas anotaciones el tipo de clase viene indicado con el nombre, pero en YOLO hay que expresarlo como entero, por ello se crea el diccionario ***class_mapping*** en el siguiente código. Posteriormente, ya viene la lógica en la cual se extrae la información de los ficheros y se realiza la conversión anterior y la necesaria para convertir las Bounndary Boxes en formato YOLO 

In [ ]:
# Dictionary that maps class names to IDs (customize this mapping as per your dataset)
class_mapping = {
    'aeroplane': 0,
    'bicycle': 1,
    'bird': 2,
    'boat': 3,
    'bottle': 4,
    'bus': 5,
    'car': 6,
    'cat': 7,
    'chair': 8,
    'cow': 9,
    'diningtable': 10,
    'dog': 11,
    'horse': 12,
    'motorbike': 13,
    'person': 14,
    'pottedplant': 15,
    'sheep': 16,
    'sofa': 17,
    'train': 18,
    'tvmonitor': 19,
}

# Function that converts to YOLO format from PASCAL information
def convert(size, box):
    dw = 1./size[0]
    dh = 1./size[1]
    x = (box[0] + box[1])/2.0
    y = (box[2] + box[3])/2.0
    w = box[1] - box[0]
    h = box[3] - box[2]
    x = x*dw
    w = w*dw
    y = y*dh
    h = h*dh
    return (x,y,w,h)

def convert_annotation(annotation_voc, out_file):
    in_file = open(annotation_voc)
    tree=ET.parse(in_file)
    root = tree.getroot()
    size = root.find('size')
    w = int(size.find('width').text)
    h = int(size.find('height').text)

    for obj in root.iter('object'):
        difficult = obj.find('difficult').text
        cls = obj.find('name').text
        if cls not in class_mapping or int(difficult) == 1:
            continue
        cls_id = class_mapping[cls]
        xmlbox = obj.find('bndbox')
        b = (float(xmlbox.find('xmin').text), float(xmlbox.find('xmax').text),
             float(xmlbox.find('ymin').text), float(xmlbox.find('ymax').text))
        bb = convert((w,h), b)
        out_file.write(" ".join([str(cls_id), " ".join([str(a) for a in bb])]) + '\n')
    in_file.close()

In [ ]:
# Paths
dataset_path = f'{path}/VOCdevkit/VOC2012'
annotations_path = os.path.join(dataset_path, 'Annotations/')
images_path = os.path.join(dataset_path, 'JPEGImages/')
labels_path = os.path.join(dataset_path, 'labels/')
os.makedirs(labels_path, exist_ok=True)


# Convert annotations

for annotation in tqdm(os.listdir(annotations_path), leave = True):
    if annotation.endswith('.xml'):
        image_id = annotation.split('.')[0]
        out_file_path = os.path.join(labels_path, image_id + '.txt')
        with open(out_file_path, 'w') as out_file:
            convert_annotation(os.path.join(annotations_path, annotation), out_file)
print('Conversions done')


### Copy files and split database

Ahora copiamos todos los ficheros de imagenes y labels en una carpeta llamada **PASCAL** que se vaya ajustando al formato de carpetas de YOLO. Por el momento se introduce en una subcarpeta llamada KFold por si más adelante para los entrenamientos se quiere introducir 10-cross-validation o similar.  

In [ ]:
def copy_matching_files(source_images_dir, source_labels_dir, dest_images_dir, dest_labels_dir):
    """
    Copies all .jpg images and .txt labels from the source directories to the destination directories,
    but only if the image and label share the same base filename.

    Parameters:
    - source_images_dir: Directory containing source images (.jpg).
    - source_labels_dir: Directory containing source labels (.txt).
    - dest_images_dir: Destination directory for images.
    - dest_labels_dir: Destination directory for labels.
    """
    # Ensure destination directories exist
    if not os.path.exists(dest_images_dir):
        os.makedirs(dest_images_dir)
    if not os.path.exists(dest_labels_dir):
        os.makedirs(dest_labels_dir)

    # Create a set of base filenames for labels
    label_filenames = {os.path.splitext(file)[0] for file in os.listdir(source_labels_dir) if file.endswith('.txt')}

    # Copy images that have a corresponding label
    for image in tqdm(os.listdir(source_images_dir), leave = True):
        base_name = os.path.splitext(image)[0]
        if image.endswith('.jpg') and base_name in label_filenames:
            shutil.copy(os.path.join(source_images_dir, image), os.path.join(dest_images_dir, image))

    # Copy corresponding labels
    for label_base in tqdm(label_filenames, leave = True):
        label_file = f'{label_base}.txt'
        shutil.copy(os.path.join(source_labels_dir, label_file), os.path.join(dest_labels_dir, label_file))
    print('Copy done')


In [ ]:
# Make sure to replace the paths with your actual paths
source_images_dir = f'{path}/VOCdevkit/VOC2012/JPEGImages'
source_labels_dir = f'{path}/VOCdevkit/VOC2012/labels'
dest_images_dir = f'{path}/PASCAL/images/Kfold'
dest_labels_dir = f'{path}/PASCAL/labels/Kfold'
copy_matching_files(source_images_dir, source_labels_dir, dest_images_dir, dest_labels_dir)

Ahora nos interesa dividir el database en train, test y valid. Al cual hay muchas sugerencias de como dividir las bases de datos para entrenar, validar y comprobar el modelo. Por el momento se dividirá de la siguiente manera, el 80% para entrenamiento (train), el 10% para validation (valid) y 10% para test. 

Los datos de entrenamiento tienen que ser diferentes a los de valid y a los de test. En cuanto a la diferencia entre los datos de valid y test, los datos de valid son utilizados para evaluar al modelo en cada epoca, mientras que los datos de test son datos que si o si, nunca ha visto el módelo y se utilizan cuando queremos evaluar el modelo una vez lo tengamos entrenado.

In [ ]:
def split_database(img_path, label_path, final_path, training_rate = 0.7, valid_rate=0.15, test_rate = 0.15):
  '''if training_rate + valid_rate + test_rate != 1:
    training_rate = 0.5
    valid_rate = 0.25
    test_rate = 0.25'''
  # Name all the files inside the original path
  files = os.listdir(img_path)
  files = [file for file in files if file.lower().endswith(('.png', '.jpg', '.jpeg'))]

  # Shuffle the files
  shuffle(files)

  # SPlit the files in training and test
  n_train = int(len(files)*training_rate)
  n_valid = int(len(files)*valid_rate)
  n_test = int(len(files)*test_rate)
  train = files[:n_train]
  valid = files[n_train:(n_train+n_valid)]
  test = files[(n_train+n_valid):(n_train+n_valid+n_test)]

  # Crea las carpetas de destino si no existen
  os.makedirs(os.path.join(final_path, 'images','train'), exist_ok=True)
  os.makedirs(os.path.join(final_path, 'images','valid'), exist_ok=True)
  os.makedirs(os.path.join(final_path, 'images','test'), exist_ok=True)
  os.makedirs(os.path.join(final_path, 'labels','train'), exist_ok=True)
  os.makedirs(os.path.join(final_path, 'labels','valid'), exist_ok=True)
  os.makedirs(os.path.join(final_path, 'labels','test'), exist_ok=True)

  for file in tqdm(train, leave = True):
      shutil.copy(os.path.join(img_path, file), os.path.join(final_path, 'images', 'train'))
      shutil.copy(os.path.join(label_path, file[:-4]+'.txt'), os.path.join(final_path, 'labels', 'train'))

  for file in tqdm(valid, leave = True):
      shutil.copy(os.path.join(img_path, file), os.path.join(final_path, 'images', 'valid'))
      shutil.copy(os.path.join(label_path, file[:-4]+'.txt'), os.path.join(final_path, 'labels', 'valid'))


  for file in tqdm(test, leave = True):
      shutil.copy(os.path.join(img_path, file), os.path.join(final_path, 'images', 'test'))
      shutil.copy(os.path.join(label_path, file[:-4]+'.txt'), os.path.join(final_path, 'labels', 'test'))

  print('Database Split')

In [ ]:
img_path = f'{path}/PASCAL/images/Kfold'
label_path = f'{path}/PASCAL/labels/Kfold'
final_path = f'{path}/PASCAL'
split_database(img_path, label_path, final_path, training_rate = 0.8, valid_rate=0.1, test_rate = 0.1)

# **PASCAL 3 Classes**

Entre las pruebas que haremos más adelante, se prueba el modelo de TinyissimoYOLO ([paper](https://arxiv.org/pdf/2306.00001)) en el cual se hacen pruebas con dos Datasets diferentes, PASCAL y WiderFace. Pero en el caso de PASCAL este se limita a 3 clases principales: personas, coches y sillas, además se le incluye la restricción de que solo puede haber 3 objetos por imagen. Por tanto creamos una nueva Base de Datos de acuerdo a estas restricciones

En la siguiente sección del código se crea una nueva subcarpeta en la carpeta de ***VOCdevkit/VOC2012*** con el nombre ***validAnnotations*** que cumpla el requisito comentado en el paper.

In [23]:
# Define the path to the annotations folder
annotations_path = f'{path}/VOCdevkit/VOC2012/Annotations/'

valid_annotations_path = f'{path}/VOCdevkit/VOC2012/validAnnotations/'

# Create the validAnnotations folder if it doesn't exist
os.makedirs(valid_annotations_path, exist_ok=True)

# Set of allowed object classes
allowed_classes = {'person', 'chair', 'car'}

# Function to check if all objects in the file are among allowed classes
def are_objects_allowed(root, allowed_classes):
    for obj in root.findall('object'):
        cls = obj.find('name').text
        if cls not in allowed_classes:
            return False
    return True

# List to store the names of the files that meet the conditions
valid_files = []

# Iterate over the XML files in the annotations folder
for annotation_file in tqdm(os.listdir(annotations_path), leave = True):
    if annotation_file.endswith('.xml'):
        # Construct the full path to the file
        file_path = os.path.join(annotations_path, annotation_file)
        # Parse the XML file
        tree = ET.parse(file_path)
        root = tree.getroot()
        # Count the number of objects in the XML file
        object_count = len(root.findall('object'))

        # Check if it meets the condition of having at most 3 objects
        # and if all objects are among the allowed classes
        if object_count <= 5 and are_objects_allowed(root, allowed_classes):
            valid_files.append(annotation_file)
            # Copy the valid XML file to the validAnnotations folder
            shutil.copy(file_path, os.path.join(valid_annotations_path, annotation_file))

100%|██████████| 17125/17125 [00:37<00:00, 462.06it/s]


Ahora creamos las nuevas labels.

In [24]:
# Paths
dataset_path = f'{path}/VOCdevkit/VOC2012'
annotations_path = os.path.join(dataset_path, 'validAnnotations/')
images_path = os.path.join(dataset_path, 'JPEGImages/')
labels_path = os.path.join(dataset_path, 'validlabels/')
os.makedirs(labels_path, exist_ok=True)


# Convert annotations
for annotation in tqdm(os.listdir(annotations_path), leave = True):
    image_id = annotation.split('.')[0]
    out_file_path = os.path.join(labels_path, image_id + '.txt')
    with open(out_file_path, 'w') as out_file:
        convert_annotation(os.path.join(annotations_path, annotation), out_file)
print('Conversions done')

100%|██████████| 6800/6800 [00:20<00:00, 333.27it/s]

Conversions done


Ahora copiamos las carpetas para que se ajusten al formato de carpetas de YOLO

In [25]:
# Make sure to replace the paths with your actual paths
source_images_dir = f'{path}/VOCdevkit/VOC2012/JPEGImages'
source_labels_dir = f'{path}/VOCdevkit/VOC2012/validlabels'
dest_images_dir = f'{path}/PASCAL_3classes/images/Kfold'
dest_labels_dir = f'{path}/PASCAL_3classes/labels/Kfold'
copy_matching_files(source_images_dir, source_labels_dir, dest_images_dir, dest_labels_dir)

100%|██████████| 6800/6800 [00:25<00:00, 268.64it/s]

Copy done


Como ahora tenemos 3 clases, vamos a modificar el parámetro de class de los fichero de tipo YOLO, para asociar nuevos valores a las clases 

In [26]:
folder_path = f'{path}/PASCAL_3classes/labels/Kfold'
for filename in tqdm(os.listdir(folder_path)):
    # Check if the current file is a .txt file
    if filename.endswith('.txt'):
        # Build the full path to the file
        file_path = os.path.join(folder_path, filename)

        # Read the content of the file
        with open(file_path, 'r') as file:
            lines = file.readlines()

        # Modify each line
        new_lines = []

        for line in lines:
            parts = line.split()
            # Change the class value to 0
            if parts[0] == '6':
              parts[0] = '0'  # Update the class value
            elif parts[0] == '14':
              parts[0] = '1'  # Update the class value
            elif parts[0] == '8':
              parts[0] = '2'  # Update the class value
            new_line = ' '.join(parts)
            new_lines.append(new_line)

        # Overwrite the file with the new content
        with open(file_path, 'w') as file:
            for line in new_lines:
                file.write("%s\n" % line)

100%|██████████| 6800/6800 [00:19<00:00, 340.52it/s]


Ahora dividimos la Base de datos

In [27]:
img_path = f'{path}/PASCAL_3classes/images/Kfold'
label_path = f'{path}/PASCAL_3classes/labels/Kfold'
final_path = f'{path}/PASCAL_3classes'
split_database(img_path, label_path, final_path, training_rate = 0.8, valid_rate=0.1, test_rate = 0.1)

100%|██████████| 680/680 [00:07<00:00, 96.56it/s] 

Database Split


# **REDUCE PASCAL**

Este va ser un dataset muy pequeño, que va además va a tener los mismos datos de train que de val y test, con el fin de hacer pruebas pequeñas de overfitting a proposito.

In [57]:
img_path = f'{path}/PASCAL_3classes/images/Kfold'
label_path = f'{path}/PASCAL_3classes/labels/Kfold'
final_path = f'{path}/reducePASCAL'
split_database(img_path, label_path, final_path, training_rate = 0.001, valid_rate=0.0, test_rate = 0.0)

100%|██████████| 6/6 [00:00<00:00, 116.97it/s]
0it [00:00, ?it/s]
0it [00:00, ?it/s]

Database Split


In [58]:
source_images_dir = f'{path}/reducePASCAL/images/train'
source_labels_dir = f'{path}/reducePASCAL/labels/train'
dest_images_dir = f'{path}/reducePASCAL/images/test'
dest_labels_dir = f'{path}/reducePASCAL/labels/test'
copy_matching_files(source_images_dir, source_labels_dir, dest_images_dir, dest_labels_dir)

100%|██████████| 6/6 [00:00<00:00, 265.15it/s]

Copy done


In [59]:
source_images_dir = f'{path}/reducePASCAL/images/train'
source_labels_dir = f'{path}/reducePASCAL/labels/train'
dest_images_dir = f'{path}/reducePASCAL/images/valid'
dest_labels_dir = f'{path}/reducePASCAL/labels/valid'
copy_matching_files(source_images_dir, source_labels_dir, dest_images_dir, dest_labels_dir)

100%|██████████| 6/6 [00:00<00:00, 351.93it/s]

Copy done


In [31]:
shutil.rmtree('VOCdevkit')

# **Download WiderFace Dataset**

In [32]:
from datasets import load_dataset

dataset = load_dataset("wider_face")

In [33]:
def convert_to_yolo_format(box, img_width, img_height):
    """
    Convierte las coordenadas de la caja delimitadora del formato (x_min, y_min, width, height)
    al formato YOLO (x_center, y_center, width, height), todos normalizados por el tamaño de la imagen.
    """
    x_min, y_min, width, height = box
    x_center = (x_min + width / 2) / img_width
    y_center = (y_min + height / 2) / img_height
    width = width / img_width
    height = height / img_height
    x_center = abs(max(min(x_center, 0.999), 0.001))  # Ajustado para incluir 1.0 como máximo y 0.0 como mínimo
    y_center = abs(max(min(y_center, 0.999), 0.001))  # Ajustado de igual forma
    width = max(width, 0.001)
    height = max(height, 0.001)    

    norm_x_min = x_center-width/2
    if norm_x_min < 0:
        width = width -2*norm_x_min
    norm_y_min = y_center-height/2
    if norm_y_min < 0:
        height = height -2*norm_y_min

    norm_x_max = x_center+width/2
    if norm_x_max > 1:
        width = width -2*(norm_x_max-1)
    norm_y_max = y_center+height/2
    if norm_y_max > 1:
        height = height -2*(norm_y_max-1)
        
    return (x_center, y_center, width, height)


In [34]:
from PIL import Image
import os
from tqdm import tqdm  # Importar tqdm

def create_Wider_folder(mode='train'):
    # Crear directorios para imágenes y etiquetas, si no existen
    os.makedirs(f"WiderFace/images/{mode}", exist_ok=True)
    os.makedirs(f"WiderFace/labels/{mode}", exist_ok=True)

    # Obtiene el total de elementos en el dataset para este modo (train, test, etc.)
    total_items = len(dataset[mode])

    # Usar tqdm para mostrar la barra de progreso con porcentaje
    for i, item in tqdm(enumerate(dataset[mode]), total=total_items, desc=f"Processing {mode} images"):
        # Cargar la imagen, asumiendo que ya es un objeto Image de PIL
        image = item['image']
        img_width, img_height = image.size

        # Guardar la imagen
        # image.save(f"WiderFace/images/{mode}/image_{i}.jpg")

        # Preparar archivo de etiquetas YOLO
        with open(f"WiderFace/labels/{mode}/image_{i}.txt", 'w') as f:
            # Suponiendo que 'boxes' es la lista de cajas delimitadoras
            for box in item['faces']['bbox']:
                # Convertir cada caja delimitadora
                yolo_box = list(convert_to_yolo_format(box, img_width, img_height))
                # Asegurarse que las coordenadas y dimensiones están dentro de los límites permitidos
                # yolo_box[0] = abs(max(min(yolo_box[0], 0.999), 0.0001))  # Ajustado para incluir 1.0 como máximo y 0.0 como mínimo
                # yolo_box[1] = abs(max(min(yolo_box[1], 0.999), 0.0001))  # Ajustado de igual forma
                # yolo_box[2] = max(yolo_box[2], 0.001)
                # yolo_box[3] = max(yolo_box[3], 0.001)
                # Escribir al archivo (suponiendo la clase 0 para todas las caras, ajusta según sea necesario)
                f.write(f"0 {yolo_box[0]} {yolo_box[1]} {yolo_box[2]} {yolo_box[3]}\n")

In [69]:
create_Wider_folder('train')

Processing train images: 100%|██████████| 12880/12880 [01:48<00:00, 118.55it/s]


In [70]:
create_Wider_folder('test')

Processing test images: 100%|██████████| 16097/16097 [01:40<00:00, 160.13it/s]


In [71]:
create_Wider_folder('validation')

Processing validation images: 100%|██████████| 3226/3226 [00:25<00:00, 125.29it/s]


Lo limitamos a que no haya archivos vacios y haya como maximo 5 objetos por imagen

In [38]:
def delete_big_txt_and_corresponding_images(source_folder, image_folder):
    """
    Moves .txt files with an empty first line from a source folder to a destination folder.

    Parameters:
    - source_folder (str): The path to the folder containing the .txt files.
    - destination_folder (str): The path to the folder where empty .txt files will be moved.
    """

    # Ensure the destination folder exists, create if not
    # Iterate over all files in the source folder
    for filename in os.listdir(source_folder):
        if filename.endswith('.txt'):  # Check if the file is a .txt file
            txt_file_path = os.path.join(source_folder, filename)  # Full path to the file
            n_lines = 0

            # Open the file and read the first line
            with open(txt_file_path, 'r') as file:
                for line in file:
                    n_lines +=1

            if n_lines > 5 or n_lines ==0:
                os.remove(txt_file_path)
                # print(f"Deleted empty .txt file: {filename}")

                # Construct the corresponding image file name and path
                image_filename = f"{os.path.splitext(filename)[0]}.jpg"
                image_file_path = os.path.join(image_folder, image_filename)

                # Check if the corresponding image file exists and delete it
                if os.path.exists(image_file_path):
                    os.remove(image_file_path)
                    # print(f"Deleted corresponding image file: {image_filename}")



In [40]:
delete_big_txt_and_corresponding_images('WiderFace/labels/train','WiderFace/images/train')

In [41]:
delete_big_txt_and_corresponding_images('WiderFace/labels/validation','WiderFace/images/validation')

In [42]:
os.rename('WiderFace/labels/validation', 'WiderFace/labels/valid')
os.rename('WiderFace/images/validation', 'WiderFace/images/valid')

# **Writting a Summay in each Dataset**

In [1]:
def summary_dataset(Dataset, num_classes, class_mapping):
    num_train_images = len(os.listdir(os.path.join(Dataset, 'images', "train")))
    num_val_images = len(os.listdir(os.path.join(Dataset, 'images', "valid")))
    num_test_images = len(os.listdir(os.path.join(Dataset, 'images', "test")))
    total_images = num_train_images + num_val_images + num_test_images
    # Building the class mapping string
    class_info = '\n'.join([f"    {key}: {value}" for key, value in class_mapping.items()])

    # Collecting data to save
    summary = f"""
    ######################################
    #              DATASET               #
    ######################################
    Dataset: {Dataset}
    Number of Classes: {num_classes}
    Number of Train Images: {num_train_images} {num_train_images/total_images*100:.2f}%
    Number of Validation Images: {num_val_images} {num_val_images/total_images*100:.2f}%
    Number of Test Images: {num_test_images} {num_test_images/total_images*100:.2f}%
    Class Mapping: 
{class_info}
    """

    # Path to save the summary file
    summary_path = os.path.join(Dataset, f"{Dataset}_summary.txt")
    print(summary_path)
    # Writing to the file
    with open(summary_path, "w") as file:
        file.write(summary)

In [75]:
class_mapping = {
    'aeroplane': 0,
    'bicycle': 1,
    'bird': 2,
    'boat': 3,
    'bottle': 4,
    'bus': 5,
    'car': 6,
    'cat': 7,
    'chair': 8,
    'cow': 9,
    'diningtable': 10,
    'dog': 11,
    'horse': 12,
    'motorbike': 13,
    'person': 14,
    'pottedplant': 15,
    'sheep': 16,
    'sofa': 17,
    'train': 18,
    'tvmonitor': 19,
}
summary_dataset('PASCAL', 20, class_mapping)

In [76]:
class_mapping = {
    'car': 0,
    'person': 1,
    'chair': 2,
}
summary_dataset(f'{path}/Datasets/PASCAL_3classes', 3, class_mapping)

In [77]:
class_mapping = {
    'car': 0,
    'person': 1,
    'chair': 2,
}
summary_dataset(f'{path}/Datasets/reducePASCAL', 3, class_mapping)

In [84]:
class_mapping = {
    'face': 1
}
summary_dataset(f'{path}/Datasets/WiderFace', 1, class_mapping)

In [31]:
class_mapping = {
    'Airplane': 1
}
summary_dataset(f'{path}/Datasets/Airbus', 1, class_mapping)

/home/jovyan/Carlos_Gonzalez/YOLO/Airbus_summary.txt


In [6]:
class_mapping = {
    'Airplane': 1
}
summary_dataset(f'{path}/Datasets/Airbus_256', 1, class_mapping)

/home/jovyan/Carlos_Gonzalez/YOLO/Datasets/Airbus_256_summary.txt
